## ELEX 4653 Lab 2

This lab provides practice on importing modules, iterators, exception handlers, and strings.

Version 2: Question 3 allows text argument to raise.

Instructions:

- Modify this notebook by adding the Python code described below.

- Test your code using the menu item `Cell  ► Run All` or `Run ► Run All Cells`

- Save the notebook (the .ipynb file) and upload it to the appropriate Assignment folder on the course web site.

#### Question 1

Write a function `myfunctions()` that returns a tuple containing the following objects in the following order.  These objects might be types, classes, methods or functions:
* math.sqrt
* re.match
* random.randint
* json.dump
* datetime.date
* urllib.request.urlopen

You should return the objects themselves, not strings with the names of the functions.  For example, `t=myfunctions()` and then `print( t[0](4), t[5]("http://google.com"))` should print `2.0 <http.client.HTTPResponse at 0x.....>` (if you have an internet connection).

#### Question 2


Write a function, `diffsum(l)`, where `l` is a list of two-element tuples.  The function should return the sum of the differences between the first item in each tuple and the second item in each tuple.

For example, if the list `l` contains `[(-1,2), (5,-2), (10,8)]` then   `diffsum(l)` should return 6.

#### Question 3

Write a function `unitabs(x)` that returns the absolute value of `x` if the absolute value of `x` is less than or equal to 1.  Otherwise it should raise the `ValueError` exception.

For example `unitabs(-0.9)` would return `0.9` but `unitabs(1.1)` would raise the `ValueError` exception.


#### Question 4

Write a function `vowelsatend(s)` that moves the vowels in the string `s` to the end of the string.  The order of the vowel and non-vowel letters should not change.  For this problem, vowels include only a, e, i, o and u.

For example, vowelsatend("orangutan") should return "rngtnoaua".

#### Question 5

Write a function `keylens(l)` that returns a dict whose keys are the values in `l` and whose values are the result of applying the `len()` function to each value.  

For example, `keylens((range(1),(1,2),"abc"))` should return `{range(0, 1): 1, (1, 2): 2, 'abc': 3}`


In [20]:
# lab validation code; do not modify
def labcheck(testing=0,ntest=10):
    '''
    Python exercise checking.
    Ed.Casas 2023-5-22
    Calls functions q<n>* and checks HMAC of return value[0].
    On mismatch prints return value[1] (function, arguments and return values).
    Setting testing=1 prints HMACs of correct results; paste into 'hashvalues'.
    Note:
    If q<n>* result not JSON-able, convert to string.
    Result order matters for comparison. Sort result if ordering not important.
    '''
    
    import base64, copy, hashlib, json, random, re, string, types 
    from random import randint
    
    # compare regex to strings that should/shouldn't match
    def checkre(pat,ok,nok):
        for s in ok:
            assert re.fullmatch(pat,s), \
                f"pattern '{pat}'\n did not match string '{s}'"
        for s in nok:
            assert not re.fullmatch(pat,s), \
                f"pattern '{pat}'\n matched string '{s}'"  
    
    # list of n words with nl letters from chars without repeats
    def randwords(n,chars=string.ascii_lowercase,nl=(2,5)):
        l = []
        while len(l)<n:
            w = ''.join([chars[randint(0,len(chars)-1)] for i in range(randint(*nl))])
            if w not in l:
                l.append(w)
        return l
    
    # convert sets to dicts and dict keys to strings so they can be sorted
    def orderkeys(o):
        if isinstance(o,set):
            return {str(k):None for k in o}
        if isinstance(o,dict):
            return {str(k):orderkeys(v) for k,v in o.items()}
        return o
    

    def Q1():
        a = [f.__name__ for f in myfunctions()]
        return a,f"myfunctions() returns {a}"

    def Q2():
        l = [(randint(-5,5),randint(-5,5)) for i in range(randint(3,5))]
        ol = copy.deepcopy(l)
        a = diffsum(l)
        return a,f"diffsum({ol}) returns {a}"

    def Q3():
        x = random.randint(-20,20)/10
        try:
            a = unitabs(x)
        except ValueError as e:
            ok = abs(x)>1 
            ex = f"raised exception {e}"
        except Exception as e:
            ok = False
            ex = f"raised exception {e}"
        else:
            ok = abs(x)<=1
            ex = f"did not raise exception"
        return ok,f"unitabs({x}) {ex}"
        
    def Q4():
        s = randwords(1,nl=(8,12))[0]
        os = copy.deepcopy(s)
        a = vowelsatend(s)
        return a,f"vowelsatend('{os}') returns '{a}'"

    def Q5():
        l = randwords(randint(3,5))
        ol = copy.deepcopy(l)
        a = keylens(l)
        return a,f"keylens(ol) returns {a}"
 
    hashvalues = '''
HAP9HAP9HAP9HAP9HAP9HAP9HAP9HAP9HAP9HAP9
p+ztS0J1/xYfREknZEo+SN5xLgOnhVRoLgOnZEo+
sifmsifmsifmsifmsifmsifmsifmsifmsifmsifm
bJA5Y9ahJTE8HzXraT/GjQqTvGYvk3wVjTrdoOod
IxKOA8tBI/MvExMSgMUxWvkFQhhIqLNw93Nn3iPv
'''.split()

    newhash = ''
    dsize = 3 # HMAC base64 digest size (bytes, use 3 or 6 for 4 or 8 char digests)
    dlen = ((dsize*8+5)//6+3)//4*4
           
    for n,f in [(n,f) for n,f in locals().items() if callable(f) and re.search(r'^[Qq]\d+.*',n)]:
        random.seed(n)      
        hashes = '0'*dlen*ntest if testing else hashvalues.pop(0)
        err = ''
        while hashes and not err:
            h, hashes = hashes[:dlen], hashes[dlen:] 
            try:
                v,s = f()
                b = json.dumps(orderkeys(v),sort_keys=True).encode()
                c = base64.b64encode(hashlib.blake2b(b,digest_size=dsize).digest()).decode()
                if testing:
                    print(s)
                    newhash += c
                else:
                    if c != h:
                        err = f"Wrong result for test {n}: {s} (HMAC={c} instead of {h})"
            except Exception as e:
                err = f"Error during test {n}: {e}"               
        if testing:
            newhash += '\n'
        else:
            print(err or f"Passed test {n}.")
            
    if testing:
        print(newhash)

labcheck(0)
